In [36]:
import numpy as np
import pandas as pd

pd.options.plotting.backend = "plotly"
from IPython.display import display
import plotly.express as px

In [37]:
fname = "Logdata Essay mini60 2023-10-31.csv"


def load_krp_file(fname):
    nrows = 12
    df_head = pd.read_csv(fname, nrows=nrows, names=["key", "value"])
    df_head = df_head.set_index("key")
    df = pd.read_csv(fname, skiprows=nrows)
    units = df.iloc[0, :]
    units.name = "units"
    cols = df.columns
    df = df.drop(0)
    for col in df.columns:
        df[col] = df[col].astype(float)
    df["Lap"] = ((df["Distance"] - df["Distance"].shift()) < 0).astype(int).cumsum()
    # df["Laptime"] = pd.NaT
    df["Starttime"] = np.where(
        (df["Distance"] - df["Distance"].shift()) < 0, df["Time"], np.NaN
    )
    df["Starttime"].iloc[0] = 0
    df["Starttime"] = df["Starttime"].fillna(method="ffill")
    df["Laptime"] = df["Time"] - df["Starttime"]

    df["Time"] = pd.to_datetime(df["Time"], unit="s")
    # df["Time"] = pd.to_timedelta(df["Time"], unit="s")

    # df["Laptime"] = pd.to_datetime(df["Laptime"], unit="s")

    df = df.set_index("Time")
    laps = df["Lap"].unique()

    laptimes = df.groupby("Lap")["Laptime"].last()[0:-1]

    return df_head, units.to_frame(), df, laps, laptimes


def get_lap_data(df, lap, index="Laptime"):
    df_lap = df[df["Lap"] == lap]
    df_lap = df_lap.set_index(index)
    return df_lap


def plot_lap_data(df, values="Engine", index="Laptime"):
    df_lap = get_lap_data(df, 0, index)
    fig = px.line(df_lap, x=df_lap.index, y=values, color="Lap")
    for lap in laps[1:]:
        df_lap = get_lap_data(df, lap, index)
        fig.add_scatter(x=df_lap.index, y=df_lap[values], mode="lines", name=str(lap))
    fig.show()


def plot_trajectory(df):
    fig = px.scatter(df, x="PosX", y="PosY", symbol="Lap", hover_name="Laptime")
    fig.show()


df_head, df_units, df, laps, laptimes = load_krp_file(fname)
display(df_head)
display(df_units)
display(df)
display(laptimes.sort_values().to_frame())

C:\Users\scell\AppData\Local\Temp\ipykernel_1200\2558702563.py:20: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\scell\AppData\Local\Temp\ipykernel_1200\2558702563.py:21: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.



value
key                                                       
Format                                     PiBoSo CSV File
Venue                        Circuit International d'Essay
Vehicle                                         CRG Mini60
User                                          Another Stig
Data Source                                Kart Racing Pro
Comment                                                NaN
Date                                              10/31/23
Time                                              18:37:43
Sample Rate                                             10
Duration                                           297.298
Segment                                            Session
Beacon Markers  64.470, 122.202, 178.989, 236.464, 293.384

units
Time             s
Distance         m
Engine         rpm
CylHeadTemp      C
WaterTemp        C
Gear           NaN
Speed         km/h
LatAcc           G
LonAcc           G
Steer          deg
Throttle         %
Brake            %
FrontBrakes      %
Clutch           %
YawVel       deg/s
PosX             m
PosY             m

Distance  Engine  CylHeadTemp  WaterTemp  Gear  \
Time                                                                      
1970-01-01 00:00:00.002    43.049  2198.0   124.991264        0.0   0.0   
1970-01-01 00:00:00.101    43.049  2177.0   124.556961        0.0   0.0   
1970-01-01 00:00:00.200    43.049  2176.0   124.134369        0.0   0.0   
1970-01-01 00:00:00.300    43.049  2176.0   123.705948        0.0   0.0   
1970-01-01 00:00:00.400    43.049  2176.0   123.280342        0.0   0.0   
...                           ...     ...          ...        ...   ...   
1970-01-01 00:04:56.900    82.974  8986.0   103.760742        0.0   0.0   
1970-01-01 00:04:57.000    85.098  8750.0   103.411682        0.0   0.0   
1970-01-01 00:04:57.101    87.192  8632.0   103.064720        0.0   0.0   
1970-01-01 00:04:57.200    89.200  8626.0   102.726723        0.0   0.0   
1970-01-01 00:04:57.300    91.201  8355.0   102.383896        0.0   0.0   

                             Speed    LatAcc    LonAcc      Steer   Throttle  \
Time                                                                           
1970-01-01 00:00:00.002   0.070633  0.002549  0.000202  -1.173652  16.666660   
1970-01-01 00:00:00.101   0.545799  0.001613  0.014398  -1.173652  18.562508   
1970-01-01 00:00:00.200   0.501256 -0.008634  0.023318  -1.173652  18.588047   
1970-01-01 00:00:00.300   0.304337 -0.000904  0.016425  -1.173652  18.588333   
1970-01-01 00:00:00.400   0.155313  0.007863  0.012276  -1.173652  18.588333   
...                            ...       ...       ...        ...        ...   
1970-01-01 00:04:56.900  65.771088  1.100487 -0.324477  12.073339   0.000000   
1970-01-01 00:04:57.000  64.806839  0.658116 -0.194999  10.702374   0.000000   
1970-01-01 00:04:57.101  63.726986  1.066653 -0.374704  12.521113   0.000000   
1970-01-01 00:04:57.200  62.621548  1.032367 -0.257688  11.918552   0.000000   
1970-01-01 00:04:57.300  61.656729  0.927830 -0.327591  13.350327   0.000000   

                           Brake  FrontBrakes  Clutch     YawVel       PosX  \
Time                                                                          
1970-01-01 00:00:00.002  0.00000          0.0     0.0   0.000484  35.729687   
1970-01-01 00:00:00.101  0.00000          0.0     0.0   0.059395  35.729839   
1970-01-01 00:00:00.200  0.00000          0.0     0.0  -0.042611  35.729771   
1970-01-01 00:00:00.300  0.00000          0.0     0.0  -0.009988  35.729748   
1970-01-01 00:00:00.400  0.00000          0.0     0.0  -0.037215  35.729797   
...                          ...          ...     ...        ...        ...   
1970-01-01 00:04:56.900  1.17302          0.0     0.0  28.847034  71.743393   
1970-01-01 00:04:57.000  1.17302          0.0     0.0  23.109797  72.994591   
1970-01-01 00:04:57.101  1.17302          0.0     0.0  36.464943  74.173767   
1970-01-01 00:04:57.200  1.17302          0.0     0.0  27.381901  75.233452   
1970-01-01 00:04:57.300  1.17302          0.0     0.0  36.080498  76.222321   

                               PosY  Lap  Starttime  Laptime  
Time                                                          
1970-01-01 00:00:00.002  136.618561    0      0.000    0.002  
1970-01-01 00:00:00.101  136.618393    0      0.000    0.101  
1970-01-01 00:00:00.200  136.617615    0      0.000    0.200  
1970-01-01 00:00:00.300  136.616974    0      0.000    0.300  
1970-01-01 00:00:00.400  136.615738    0      0.000    0.400  
...                             ...  ...        ...      ...  
1970-01-01 00:04:56.900   98.704651    5    293.401    3.499  
1970-01-01 00:04:57.000   97.395935    5    293.401    3.599  
1970-01-01 00:04:57.101   96.055145    5    293.401    3.700  
1970-01-01 00:04:57.200   94.702423    5    293.401    3.799  
1970-01-01 00:04:57.300   93.289101    5    293.401    3.899  

[2974 rows x 19 columns]

Laptime
Lap         
2     56.600
4     56.799
3     57.401
1     57.699
0     64.401

In [152]:
df.groupby("Lap")["Time"].last() - df.groupby("Lap")["Time"].first()

Lap
0    64.399
1    57.699
2    56.600
3    57.401
4    56.799
5     3.899
Name: Time, dtype: float64

In [38]:
df["Distance"].plot()

C:\Users\scell\AppData\Roaming\Python\Python310\site-packages\_plotly_utils\basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [39]:
df["Engine"].plot()

C:\Users\scell\AppData\Roaming\Python\Python310\site-packages\_plotly_utils\basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [40]:
plot_lap_data(df, "Engine")

In [41]:
data_cols = df.columns.drop(["Distance", "Lap", "Laptime", "Starttime", "PosX", "PosY"])
data_cols

Index(['Engine', 'CylHeadTemp', 'WaterTemp', 'Gear', 'Speed', 'LatAcc',
       'LonAcc', 'Steer', 'Throttle', 'Brake', 'FrontBrakes', 'Clutch',
       'YawVel'],
      dtype='object')

In [42]:
from IPython.display import display, HTML

display(HTML("<style>div.output_scroll { height: 44em; }</style>"))

In [43]:
for data_col in data_cols:
    plot_lap_data(df, data_col)

In [44]:
plot_trajectory(df)

In [45]:
for data_col in data_cols:
    plot_lap_data(df, data_col, "Distance")

In [46]:
df = df.reset_index()


In [47]:
df["Time"] = (df["Time"] - pd.to_datetime(0)).dt.total_seconds()
df

Time  Distance  Engine  CylHeadTemp  WaterTemp  Gear      Speed  \
0       0.002    43.049  2198.0   124.991264        0.0   0.0   0.070633   
1       0.101    43.049  2177.0   124.556961        0.0   0.0   0.545799   
2       0.200    43.049  2176.0   124.134369        0.0   0.0   0.501256   
3       0.300    43.049  2176.0   123.705948        0.0   0.0   0.304337   
4       0.400    43.049  2176.0   123.280342        0.0   0.0   0.155313   
...       ...       ...     ...          ...        ...   ...        ...   
2969  296.900    82.974  8986.0   103.760742        0.0   0.0  65.771088   
2970  297.000    85.098  8750.0   103.411682        0.0   0.0  64.806839   
2971  297.101    87.192  8632.0   103.064720        0.0   0.0  63.726986   
2972  297.200    89.200  8626.0   102.726723        0.0   0.0  62.621548   
2973  297.300    91.201  8355.0   102.383896        0.0   0.0  61.656729   

        LatAcc    LonAcc      Steer   Throttle    Brake  FrontBrakes  Clutch  \
0     0.002549  0.000202  -1.173652  16.666660  0.00000          0.0     0.0   
1     0.001613  0.014398  -1.173652  18.562508  0.00000          0.0     0.0   
2    -0.008634  0.023318  -1.173652  18.588047  0.00000          0.0     0.0   
3    -0.000904  0.016425  -1.173652  18.588333  0.00000          0.0     0.0   
4     0.007863  0.012276  -1.173652  18.588333  0.00000          0.0     0.0   
...        ...       ...        ...        ...      ...          ...     ...   
2969  1.100487 -0.324477  12.073339   0.000000  1.17302          0.0     0.0   
2970  0.658116 -0.194999  10.702374   0.000000  1.17302          0.0     0.0   
2971  1.066653 -0.374704  12.521113   0.000000  1.17302          0.0     0.0   
2972  1.032367 -0.257688  11.918552   0.000000  1.17302          0.0     0.0   
2973  0.927830 -0.327591  13.350327   0.000000  1.17302          0.0     0.0   

         YawVel       PosX        PosY  Lap  Starttime  Laptime  
0      0.000484  35.729687  136.618561    0      0.000    0.002  
1      0.059395  35.729839  136.618393    0      0.000    0.101  
2     -0.042611  35.729771  136.617615    0      0.000    0.200  
3     -0.009988  35.729748  136.616974    0      0.000    0.300  
4     -0.037215  35.729797  136.615738    0      0.000    0.400  
...         ...        ...         ...  ...        ...      ...  
2969  28.847034  71.743393   98.704651    5    293.401    3.499  
2970  23.109797  72.994591   97.395935    5    293.401    3.599  
2971  36.464943  74.173767   96.055145    5    293.401    3.700  
2972  27.381901  75.233452   94.702423    5    293.401    3.799  
2973  36.080498  76.222321   93.289101    5    293.401    3.899  

[2974 rows x 20 columns]

In [48]:
def get_lap_data(df, index="Distance"):
    lap_data = {}
    for values in df.columns:
        if values not in [index, "Lap"]:
            lap_data[values] = pd.pivot_table(df, values=values, index=index, columns="Lap")
            lap_data[values] = lap_data[values].interpolate()
    return lap_data

lap_data = get_lap_data(df)
lap_data["Engine"].plot()

In [49]:
px.scatter(df[df["Lap"] == 4], x="PosX", y="PosY", color="Throttle", hover_name="Laptime", color_continuous_scale="YlOrBr")

In [206]:
import math

def distance(posx, posy, sectors):
    def dist_from_sect(posx, posy, sector):
        sectorx, sectory = sector
        return math.sqrt((posx - sectorx) ** 2 + (posy - sectory) ** 2)        
    dist_min = dist_from_sect(posx, posy, sectors[0])
    for sector in sectors:
        dist = dist_from_sect(posx, posy, sector)
        if dist < dist_min:
            dist_min = dist
    return dist_min

def calculate_sector(df, sectors):
    sector = 1
    df["InStartSector"] = False
    #df.loc[df.index[0], "InStartSector"] = True
    df["Sector"] = sector
    start_sector_time = 0
    for idx, row in df.iterrows():
        time = row["Time"]
        dist = distance(row["PosX"], row["PosY"], sectors)
        if dist < 10:
            if time > start_sector_time + 5.0:
                start_sector_time = time
                df.loc[idx, "InStartSector"] = True
                sector = sector + 1
                if sector > len(sectors):
                    sector = 1
        df.loc[idx, "Sector"] = sector
    return df


sectors = [
    #(11.25781, 110.9268),
    (-6.439126, 111.060745),
    (24.86974, -3.482062),
    (2.538615, 13.90147)
]
df = calculate_sector(df, sectors)

#px.scatter(df[df["Lap"] == 4], x="PosX", y="PosY", color="InStartSector", hover_name="Time")
px.scatter(df[df["Lap"] == 2], x="PosX", y="PosY", color="Sector", hover_name="Time")

Lap
0    64.401
1    57.699
2    56.600
3    57.401
4    56.799
Name: Laptime, dtype: float64

In [224]:
df_laptime_sector = df.groupby(["Lap", "Sector"])["Laptime"].last() - df.groupby(["Lap", "Sector"])["Laptime"].first()
df_laptime_sector = df_laptime_sector.reset_index().pivot_table(values="Laptime", columns="Sector", index="Lap").iloc[1:-1, :]
df_laptime_sector.iloc[:, 0] = df_laptime_sector.iloc[:, 0] - df_laptime_sector.iloc[:, 1:].sum(axis=1)
df_laptime_sector

Sector       1       2       3
Lap                           
1       20.299  19.600  17.800
2       19.900  19.099  17.601
3       19.900  19.901  17.600
4       19.898  19.201  17.700

In [50]:
px.scatter(df[df["Lap"] == 4], x="PosX", y="PosY", color="Brake", hover_name="Laptime", color_continuous_scale="YlOrBr")

In [82]:
df["AbsLatAcc"] = abs(df["LatAcc"]) > 1.5
px.scatter(df[df["Lap"] == 4], x="PosX", y="PosY", color="AbsLatAcc", hover_name="Laptime", color_continuous_scale="YlOrBr")

In [51]:
px.scatter(df[df["Lap"] == 4], x="PosX", y="PosY", color="Speed", hover_name="Laptime", color_continuous_scale="YlOrBr")

In [71]:
px.scatter(df[(df["Lap"] == 4) & (df["Laptime"] > 0) & (df["Laptime"] < 7)], x="PosX", y="PosY", color="Speed", hover_name="Laptime", color_continuous_scale="YlOrBr")

In [70]:
px.scatter(df[(df["Lap"] == 4)], x="LatAcc", y="LonAcc", color="Speed", hover_name="Laptime", color_continuous_scale="YlOrBr")